In [1]:
import numpy as np
import pandas as pd
import os
from matplotlib.ticker import AutoMinorLocator
from matplotlib import pyplot as plt, ticker as mticker
import folium

In [2]:
# font sizes
titleSize = 30
axisLabelSize = 24
tickLabelSize = 14
legendTextSize = 14

# colours
backgroundColor = '#292929'
legendColor = 'w'

# misc
standardCanvasHeight = 8
standardCanvasWidth = 16
DPI = 300 #Dots per inch of plots 
cwd = os.getcwd()

In [3]:
summits = pd.read_csv(f'{cwd}/pinnaclePoints.txt', sep=",")

numSummits = len(summits)
print(f'Number of Points: {numSummits}')
summits30 = summits.query('prominence_m < 300')
numSummits30 = len(summits30)
print(f'Number of Points (< 300 m): {numSummits30}')
summits300 = summits.query('prominence_m >= 300 and prominence_m < 3000')
numSummits300 = len(summits300)
print(f'Number of Points (> 300 m and < 3000 m): {numSummits300} ({round(numSummits300/numSummits, 2)} of points)')
summits3000 = summits.query('prominence_m >= 3000')
numSummits3000 = len(summits3000)
print(f'Number of Points (> 3000 m): {numSummits3000} ({round(numSummits3000/numSummits, 3)} of points)')

print('\n')
print(summits.describe())

Number of Points: 2933
Number of Points (< 300 m): 2314
Number of Points (> 300 m and < 3000 m): 568 (0.19 of points)
Number of Points (> 3000 m): 51 (0.017 of points)


          latitude    longitude  elevation_m  prominence_m
count  2933.000000  2933.000000  2933.000000   2933.000000
mean     14.706553    18.632976   726.217661    345.978554
std      41.063665    83.041802  1006.904432    741.910288
min     -89.658100  -179.354200     6.500000     30.500000
25%     -17.039200   -60.071900   169.600000     37.400000
50%      22.010600    25.682200   355.300000     67.500000
75%      51.297200    79.855000   780.200000    220.200000
max      83.318300   179.024200  8737.800000   8737.800000


In [8]:
earthRadius = 6371146 # in m

def horizonDistance(prm):
    return np.sqrt(2*earthRadius*prm)

def getHorizonColor(prominence):
    if prominence >= 3000:
        return 'red'
    elif prominence >= 300:
        return 'orange'
    else:
        return 'yellow'

def addCircleToMap(summit): 
    
    pinnaclePointRank = summits.prominence_m.rank(ascending=False)[summits.prominence_m == summit.prominence_m].iloc[0]
    
    toolTip = (f'Latitude: {round(summit.latitude, 4)}<br>Longitude: {round(summit.longitude, 4)}<br>' 
             + f'Prominence: {summit.prominence_m} m<br>Elevation: {summit.elevation_m} m<br>'
             + f'Horizon Distance: {round(horizonDistance(summit.prominence_m)/1000, 1)} km')
        
    folium.Circle(
        location = [summit.latitude, summit.longitude],
        radius = horizonDistance(summit.prominence_m),
        fill = True,
        fill_color = getHorizonColor(summit.prominence_m),
        fill_opacity = 0.33,
        weight = 0.3,
        color = 'black',
        tooltip = toolTip
    ).add_to(horizonMap)
    
    folium.RegularPolygonMarker(
        location = [summit.latitude, summit.longitude],
        number_of_sides=3,
        radius = 3,
        fill = True,
        fill_color = 'black',
        fill_opacity = 1,
        weight = 0,
        gradient = False,
        rotation = 30,
        tooltip = toolTip
    ).add_to(horizonMap)
    
horizonMap = folium.Map(location=[0, 0], zoom_start=2, tiles='Stamen Terrain')
summits.apply(lambda summit: addCircleToMap(summit), axis=1)    

legend_html = """
    <div style="
        background-color: rgba(255, 255, 255, 0.9);
        padding: 5px;
        font-size: 12px;
        position: absolute;
        top: 10px;
        right: 10px;
        z-index: 1000;
    ">
        <div style="display: flex; align-items: center; cursor: pointer;" onclick="toggleLegend()">
            <div id="chevronIcon" style="margin-left: 11px; margin-right: 15px; width: 10px; height: 10px; 
                border-style: solid; border-width: 0 2px 2px 0; transform: rotate(45deg);"></div>
            <h4 style="margin: 0; margin-right: 135px;">Earth's Pinnacle Points</h4>
        </div>
        <div id="legendContent" style="display: none; margin-top: 5px;">
            <p style="margin: 0;">
                <div class="row">
                    <div class="col-1" style="margin-left: 20px; margin-right: -2px; margin-top: 5px">
                        <svg width="6" height="6">
                            <polygon points="0,6 3,0 6,6" fill="black" />
                        </svg>
                    </div>
                    <div class="col" style="margin-top: 7px">
                        <div class="col">Pinnacle point [Count: 2933]</div>
                    </div>
                </div>
            </p>
            <p style="margin: 0;">
                <div class="row">
                    <div class="col-1" style="margin-left: 12px; margin-right: 6px; margin-top: 5px">
                        <svg width="22" height="22">
                            <circle cx="11" cy="11" r="10" fill="rgba(255, 255, 0, 0.33)" stroke="black" stroke-width="0.3" />
                        </svg>
                    </div>
                    <div class="col">Approximate area that can be seen for pinnacle points with<br>30 m &le; prominence < 300 m [Count: 2314]</div>
                </div>
            </p>
            <p style="margin: 0;">
                <div class="row">
                    <div class="col-1" style="margin-left: 12px; margin-right: 6px; margin-top: 5px">
                        <svg width="22" height="22">
                            <circle cx="11" cy="11" r="10" fill="rgba(255, 165, 0, 0.33)" stroke="black" stroke-width="0.3" />
                        </svg>
                    </div>
                    <div class="col">Approximate area that can be seen for pinnacle points with<br>300 m &le; prominence < 3000 m [Count: 568]</div>
                </div>        
            </p>
            <p style="margin: 0;">
                <div class="row">
                    <div class="col-1" style="margin-left: 12px; margin-right: 6px; margin-top: 5px">
                        <svg width="22" height="22"">
                            <circle cx="11" cy="11" r="10" fill="rgba(255, 0, 0, 0.33)" stroke="black" stroke-width="0.3" />
                        </svg>
                    </div>
                    <div class="col">Approximate area that can be seen for pinnacle points with<br>prominence &ge; 3000 m [Count: 51]</div>
                </div>
            </p>
        </div>
    </div>

    <script>
        function toggleInfoWindow() {
            var infoWindow = document.getElementById("infoWindow");
            var infoIcon = document.getElementById("informationIcon");

            if (infoWindow.style.display === "block") {
                infoWindow.style.display = "none";
                infoIcon.style.fill = "rgba(255, 255, 255, 0.9)";
            } else {
                infoWindow.style.display = "block";
                infoIcon.style.fill = "rgba(255, 255, 0, 0.9)";
            }
        }
    </script>

    <script>
        function toggleLegend() {
            var contentDiv = document.getElementById("legendContent");
            var chevronIcon = document.getElementById("chevronIcon");

            if (contentDiv.style.display === "block") {
                contentDiv.style.display = "none";
                chevronIcon.style.transform = "rotate(45deg)";
            } else {
                contentDiv.style.display = "block";
                chevronIcon.style.transform = "rotate(225deg)";
            }
        }
    </script>
"""

horizonMap.get_root().html.add_child(folium.Element(legend_html))

horizonMap.get_root().html.add_child(folium.Element(f'''
    <div id="infoIcon" style="position: absolute; bottom: 15px; right: 5px; cursor: pointer; z-index: 1001;">
        <svg id="informationIcon" width="50" height="50" viewBox="0 0 50 50" fill="white" stroke="black" stroke-width="4" 
            stroke-linecap="round" stroke-linejoin="round" onclick="toggleInfoWindow()">
            <circle cx="24" cy="24" r="20"></circle>
            <line x1="24" y1="32" x2="24" y2="24"></line>
            <line x1="24" y1="16" x2="24" y2="16"></line>
        </svg>
    </div>
    <div id="infoWindow" style="display: none; overflow-y: auto; position: absolute; top: 50%; left: 50%; 
        transform: translate(-50%, -50%); background-color: rgba(255, 255, 255, 0.9); padding: 10px; width: 800px; 
        height: 400px;  z-index: 1000;">
        <h3>Definitions</h3>
        <p>A <b>pinnacle point</b> is a point from which no higher point can be seen.
        </p>
        <p>More specifically, 
            a pinnacle point is a point with zero <b>inferiority</b>, where inferiority is defined as the maximum elevation 
            that can be seen in a direct line of sight from a point minus the point's elevation. 
            Since all points can see themselves, the minimum possible inferiority is zero.
        </p> 
        <h3>Finding Pinnacle Points</h3>
        <p>Thanks to Kai Xu for inspiring my search for pinnacle points with his own search for 
            <a href="https://ototwmountains.com/">on-top-of-the-world mountains</a>. Also, thanks to Andrew Kirmse 
            for his list of <a href="https://www.andrewkirmse.com/prominence-update-2023#h.cap6s838fwux">11,866,713 summits</a> 
            with a prominence greater than 100 ft. I would not have been able to get this project off the 
            ground without it. Even with it, I have to make many approximations. I assume the Earth to be a 
            sphere instead of an oblate spheroid, and I do not take the effect of 
            atmospheric refraction into account.
        </p>
        <p>For all 11,866,713 summits, I find the summit's <b>horizon distance</b> defined as &radic;(2*R_earth*Prominence). 
            Prominence is used instead of elevation since prominence is a 
            better measure of a summit's rise above its surroundings. I use an algorithm to find all 
            summits that have no higher summits in view. I define two summits to be in view if their 
            geospatial distance is less than the sum of their horizon distances. This is far from ideal. 
            Not only is the equation for horizon distance an approximation, the very concept of horizon 
            distance is flawed. Ultimately, viewshed analysis needs to be done to find Earth's pinnacle points 
            with greater confidence and accuracy. I am investigating how to best do this given the high computational 
            cost of viewshed analysis.
        </p>
        <p>Check out the latest on <a href="https://github.com/jgbreault/PinnaclePoints">my github</a>. 
            Contact me at jamiegbreault@gmail.com.
        </p>
    </div>
'''))

horizonMap

In [9]:
horizonMap.save('index.html')

In [6]:
def findClosestPinnaclePoints(lat, lng, summits=summits, num=5):
    latRad, lngRad = np.radians(lat), np.radians(lng)

    deltaLat = np.radians(summits.latitude) - latRad
    deltaLng = np.radians(summits.longitude) - lngRad

    # Apply Haversine formula to calculate distances
    a = np.sin(deltaLat/2)**2 + np.cos(deltaLat)*np.cos(np.radians(summits.latitude))*np.sin(deltaLng/2)**2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1 - a))
    distances = earthRadius/1000 * c
    
    distances = distances.sort_values().round(1)
    closestDistances = distances.head(num)
    closestPinnaclePoints = summits.loc[closestDistances.index]
    closestPinnaclePoints['distance_km'] = closestDistances
        
    return closestPinnaclePoints

findClosestPinnaclePoints(45.4236, -75.7009, num=8)

latitude  longitude  elevation_m  prominence_m  distance_km
628    46.2489   -74.5594        937.0         538.4        139.9
942    45.6489   -78.2569        582.7         386.5        238.9
768    48.8042   -73.5900        737.3         327.6        421.4
297    44.2705   -71.3034       1916.6        1877.0        433.1
968    48.4867   -78.7725        570.5         273.1        439.6
998    44.3714   -80.2481        550.8         289.3        443.2
1045   49.6211   -76.9500        529.1         212.7        479.9
811    47.3175   -80.7525        691.0         388.4        508.1

Ideas for improvment:
- find an API that allows you to download DEM tiles
- programatically download, analyze, and delete tiles
- don't do viewshed analysis, just do line of sight anaylsis
- same as before, start with highest elevation point, work your way down
- delete all points in view, only check in view if within 538 km (max line of sight on earth)
- only check extremal points, since pinnacle points are a subset (count: ~6.5k)
- the peak in the DEM might be slightly diffrerent than that given lat-lngs, so set the origin at the peak of the line of sight plot, set the end to be the peak within the final resolution length

Problems:
- line of sight analysis to every near summit sounds a lot like viewshed analysis, which is SLOW

In [7]:
# Taking a look at On-Top-Of-The-World Mountains

cwd = os.getcwd()
ototw = pd.read_csv(f'{cwd}/misc/ototw_p300m.csv')
ototw = ototw[['latitude', 'longitude', 'jut_m']]
ototw.describe()

latitude    longitude        jut_m
count  6464.000000  6464.000000  6464.000000
mean     24.399308    29.877093   306.352823
std      33.722515    90.299667   276.619491
min     -86.765600  -179.810300     0.169398
25%       1.358350   -52.151150   120.692481
50%      29.688750    37.436550   232.290982
75%      51.030800   107.065550   404.623358
max      83.374700   179.986400  3148.635225